In [ ]:
import data.tools.zplot2 as zp
from data.tools import zed

If you don't want to see all the logging error messages in your notebook, add the following lines:

In [ ]:
#from absl import logging
#logging.set_verbosity(logging.WARNING)

Load the data from our simulated run

In [ ]:
uri = PASTE URI HERE

We can load several topics at the same time with ZED

In [ ]:
topics = ["/planner/hero_state", "/planner/tracker/control", "/planner/decision"]

In [ ]:
data = zed.from_chum(runid=uri,
                     topics=topics)

We can see the list of topics available with zed

In [ ]:
zed.list_available_topics(uri)

In [ ]:
a_x = data.planner_hero_state[:].body_acceleration.a_x
a_y = data.planner_hero_state[:].body_acceleration.a_y
a_z = data.planner_hero_state[:].body_acceleration.a_z

In [ ]:
x=data.planner_hero_state[:].pose.x
y=data.planner_hero_state[:].pose.y
hero_time=data.planner_hero_state[:].timestamp

The returned data is a numpy array

In [ ]:
type(y)

We can multiply every element by 2, for example.

In [ ]:
y_double = y*2

Let's plot our simulation data.

We first set the output format to JupyterNotebook, to have inline plots.

In [ ]:
zp.set_output_format(zp.JupyterNotebook)

In [ ]:
zp.plot(x=hero_time, y=x)
zp.show()

A pretty basic, isn't it? Let's add more options.

In [ ]:
zp.figure(                                                                  
    name="HeroState Figure",                                                
    show_title=True,                                                        
    grid=True,                                                              
    legend=True,                                                            
    x_label="Time (s)",                                                
    y_label="HeroState y pose (m)",                                                
)                                                                           

zp.plot(x=hero_time, y=y, name="HeroState Plot", linespec="g--")

zp.figure(                                                                  
    name="HeroState Figure 2x",
    show_title=True,
    grid=True,
    legend=True,
    x_label="Time (s)",                                                
    y_label="HeroState y pose * 2 (m)",                                                
)                                                                           
zp.plot(x=hero_time, y=y_double)
zp.figure(                                                                  
    name="Accelerations",                                                
    show_title=True,                                                        
    grid=True,                                                              
    legend=True,                                                            
    x_label="Time(ns)",                                                
    y_label="Acceleration",                                                
)                   
zp.plot(x=hero_time, y=a_x, name="x acc", linespec="r-")
zp.plot(x=hero_time, y=a_y, name="y acc", linespec="b-")
zp.plot(x=hero_time, y=a_z, name="z acc", linespec="y-")
zp.show()

Let's calculate the derivative of velocity, and compare againt acceleration

In [ ]:
v_x = data.planner_hero_state[:].body_velocity.v_x

In [ ]:
import numpy as np
d_t = np.diff(hero_time)
d_x = np.diff(x)
d_vx = np.diff(v_x)

In [ ]:
vx_der = d_vx / d_t

In [ ]:
zp.figure(                                                                  
    name="Acceleration",                                                
    show_title=True,                                                        
    grid=True,                                                              
    legend=True,                                                            
    x_label="Time(s)",                                                
    y_label="Acceleration(m/s^2)",                                                
)                   
zp.plot(x=hero_time[2:], y=a_x[2:], name="x acc", linespec="r-")
zp.figure(
    name="Vx derivative",
    show_title=True,
    grid=True,
    legend=True,
    x_label="Time(s)",
    y_label="Acceleration(m/s^2)")
zp.plot(x=hero_time[1:], y=vx_der, name="d_vx/ dt", linespec="b-")

In [ ]:
zp.show()

# Reproducibility

As we have mentioned, [ZED](https://git.zooxlabs.com/zooxco/driving/blob/master/data/tools/zed/README.md) also supports reproducibility.


Let's first load `/planner/hero_state` by itself.

In [ ]:
data = zed.from_chum(runid=uri,
                     topics=["/planner/hero_state"])

In [ ]:
len(data.planner_hero_state[:])

We have 13244 messages in that topic.

Let's see what happens when we add `/planner/tracker/control` as the parent topic.

In [ ]:
data_tracker = zed.from_chum(runid=uri,
                             topics=["/planner/hero_state"],
                             parent='/planner/tracker/control',
                             policy=zed.AssociationPolicy.REPRO)

In [ ]:
len(data_tracker.planner_hero_state[:])

When we use reproducibility, the child topic is downsampled if it runs at a higher frequency that the parent topic. In this case `/planner/hero_state` runs at 200Hz, while `/planner/tracker/control` runs at 50Hz. That's why we see less samples now.

Let's see what happens if the parent is `/planner/decision`

In [ ]:
data_decision = zed.from_chum(runid=uri,
                              topics=["/planner/hero_state"],
                              parent='/planner/decision',
                              policy=zed.AssociationPolicy.REPRO)

In [ ]:
len(data_decision.planner_hero_state[:])

`/planner/decision` runs at 10Hz, so the number of messages now is approximately 20 times less than when we originally loaded `/planner/hero_state`

In [ ]:
zp.figure(                                                                  
    name="HeroState Figure",                                                
    show_title=True,                                                        
    grid=True,                                                              
    legend=True,                                                            
    x_label="x coordinates",                                                
    y_label="y coordinates",                                                
)                                                                           

zp.plot(x=data.planner_hero_state[:1000].timestamp,
        y=data.planner_hero_state[:1000].pose.x,
        name="HeroState Plot", linespec="go")                                                                    
zp.plot(x=data_tracker.planner_hero_state[:250].timestamp,
        y=data_tracker.planner_hero_state[:250].pose.x,
        name="HeroState Plot", linespec="ro") 
zp.plot(x=data_decision.planner_hero_state[:50].timestamp,
        y=data_decision.planner_hero_state[:50].pose.x,
        name="HeroState Plot", linespec="bo") 
zp.show()

# Changing simulation parameters
In this section we are going to make a small change in the vehicle configuration and see how the results differ.

Go to `//vehicle/planner/node/planner_configuration.pbtxt` and modify min and max steering angle rates in lines 430 and 431. Let's set them to `0.07`

Now we will see a `NOGO`. Let's see the pose and steering angle.

In [ ]:
uri_steering = COPYU URI OF NEW SIMULATION HERE

In [ ]:
data_steering = zed.from_chum(runid=uri_steering,
                              topics=topics)

In [ ]:
x_original = data.planner_hero_state[:].pose.x
y_original = data.planner_hero_state[:].pose.y
x_limits = data_steering.planner_hero_state[:].pose.x
y_limits = data_steering.planner_hero_state[:].pose.y

In [ ]:
steering_angle_north_original = data.planner_hero_state[:].steering_angle_north
steering_angle_north_limits = data_steering.planner_hero_state[:].steering_angle_north

In [ ]:
hero_time_limits=data_steering.planner_hero_state[:].timestamp

In [ ]:
zp.figure(                                                                  
    name="Pose - Modified steering limits",                                                
    show_title=True,                                                        
    grid=True,                                                              
    legend=True,                                                            
    x_label="x",                                                
    y_label="y",
)
zp.plot(x=x, y=y, name="Original sim", linespec="r-")
zp.plot(x=x_limits, y=y_limits, name="Tighter steering limits", linespec="b-")

zp.figure(                                                                  
    name="Steering Angle North - Modified steering limits",                                                
    show_title=True,                                                        
    grid=True,                                                              
    legend=True,                                                            
    x_label="time(s)",                                                
    y_label="SAN (rad)",
)

zp.plot(x=hero_time, y=steering_angle_north_original, name="SAN orig", linespec="b-")
zp.plot(x=hero_time_limits, y=steering_angle_north_limits, name="SAN lim", linespec="r-")

zp.show()